In [44]:
import pickle
from sc2.game_info import GameInfo

import numpy as np
from scipy import ndimage
import plotly.express as px
import plotly.graph_objects as go

In [45]:
import sys
sys.path.append("../bot")

from utils.poisson_multigrid import mg_opt, convolve_jacobi

In [46]:
with open("../resources/Site Delta AIE.pkl", "rb") as f:
    game_info: GameInfo = pickle.load(f)

In [47]:
b = game_info.pathing_grid.data_numpy.T
b *= (convolve_jacobi(b) > 0)
px.imshow(b)

In [48]:
f = b.astype(float)
f += np.random.rand(*f.shape)
f += 1
f[:f.shape[0]//2,:] *= -1.0
f[:f.shape[0]//2,:] = 0.0
f *= b
f -= f.sum() / b.sum()
f /= np.max(abs(f))
#f /= np.prod(f.shape)
px.imshow(f)

In [49]:
(f * b).sum()

1.1652900866465643e-12

In [50]:
x = np.zeros_like(f)
for _ in range(3):
    x = mg_opt(x, f, b)
px.imshow(np.where(b, x, np.nan))

In [53]:
x = np.zeros_like(b)
for i in range(1000):
    x = mg_opt(x, f, b)
px.imshow(np.where(b, x, np.nan))

In [52]:
g = b[:-1,:-1,np.newaxis] * np.dstack((
    np.diff(x, axis=0)[:,:-1],
    np.diff(x, axis=1)[:-1,:],
    np.zeros_like(x)[:-1,:-1],
))
g /= 1e-10 + np.linalg.norm(g, axis=2, keepdims=True)
px.imshow(g, zmin=-1, zmax=1)